# Install all necessary packages, hopefully should work without needing to go into pawsey directories with singularity shell

# MOVE The transformers folder from /src/ in the DNABERT repo to where packages are stored /home/mgill/.local/lib/python3.8/site-package

In [ ]:
#Bug where it installs wrong transformers for some reason in wrong spot, this should fix it

!python3 -m pip install --editable .
!python3 -m pip install torch==1.4 torchvision
!python3 -m pip install tensorflow tensorboardX tensorboard seqeval pyahocorasick scipy statsmodels biopython pandas pybedtools sentencepiece==0.1.91 scikit-learn>=0.22.2
!python3 -m pip install ipywidgets

####MOVE The transformers folder from /src/ in the DNABERT repo to where packages are stored /home/mgill/.local/lib/python3.8/site-package

In [ ]:
!TMPDIR=/home/mgill/ python3 -m pip install scikit-cuda fastai==1.0.61 biopython

In [ ]:
!TMPDIR=/home/mgill/ python3 -m pip install networkx

In [ ]:
!pip list

In [1]:
from fastai import *
from fastai.text import *
from Bio import Seq
from Bio.Seq import Seq
from Bio import SeqIO
from Bio.SeqRecord import SeqRecord
from Bio.SeqFeature import FeatureLocation, CompoundLocation
import networkx as nx
import pandas as pd

# Before continuing on ensure you have run script to retrieve fasta from GFF3s (from cantata and ensembl) and random streteches of DNA

### Run Script Below. Needs to have a ref genome file ending in {whatever}_ref.fa
### Needs to have genome info file ending in {whatever}_genome_file.genome
### both need to be in same folder as script

# run bash script below on server with pandas and numpy
# arg1 being url for lncrna, arg2 url for mrna, change URL for each crop

bash create_fasta_from_url.sh http://cantata.amu.edu.pl/DOWNLOADS/Arabidopsis_thaliana_lncrnas.gtf ftp://ftp.ensemblgenomes.org/pub/plants/release-51/gff3/arabidopsis_thaliana/Arabidopsis_thaliana.TAIR10.51.gff3.gz

# Preprocess Data From Fasta of lncrna, mrna and random to TSV's
### Based upon g-ulmfit conversion of fasta to csv
### then DNABERT (with some of my edits) from csv format to kmer tab delimited TSV's

In [2]:
#set filenames to string
#mrna = 'mrna_ensembl.gff3unique.gff3_flanked.fa'
lncrna1 = 'Arabidopsis_thaliana_lncrnas.fa'
#lncrna2 = 'lncRNAs_without_gene_cantata.gff3unique.gff3_flanked.fa'
randrna1 = 'random_intervals.fa'
#randrna2 = 'random_intervals_flanked_wo.fa'

In [3]:
#read fasta file
#creates DF with column of fasta string and a 2nd column of whether it was mRNA, lncRNA etc.
def parse_fasta(filename, label):
    fasta = SeqIO.parse(filename, 'fasta')
    fs = [i for i in fasta]
    seqs = [str(i.seq) for i in fs]
    df = pd.DataFrame(seqs, columns=['Sequence'])
    df['Target'] = label
    df = df.drop_duplicates()
    return df

In [4]:
#create df for each set of transcripts
#mrna_df = parse_fasta(mrna, "not_lncRNA")
lncrna_df1 = parse_fasta(lncrna1, "lncRNA")
#lncrna_df2 = parse_fasta(lncrna2, "lncRNA")
random_df1 = parse_fasta(randrna1, "not_lncRNA")
#random_df2 = parse_fasta(randrna2, "not_lncRNA")

In [ ]:
#mrna_df=mrna_df.sample(1000)
#mrna_df.shape
#print(mrna_df)

In [ ]:
#random_df=random_df.sample(4000)
#random_df.shape
#print(random_df)

In [ ]:
total = 0
for x in range(0,random_df1.shape[0]):
    y=len(random_df1.iloc[x]["Sequence"])
    if(y>total):
        total=y
print(total)
    
print(str(total/random_df1.shape[0]))

total = 0
for x in range(0,random_df2.shape[0]):
    y=len(random_df2.iloc[x]["Sequence"])
    if(y>total):
        total=y
print(total)
    
print(str(total/random_df2.shape[0]))

total = 0
for x in range(0,lncrna_df1.shape[0]):
    y=len(lncrna_df1.iloc[x]["Sequence"])
    if(y>total):
        total=y
print(total)
    
print(str(total/lncrna_df1.shape[0]))

total = 0
for x in range(0,lncrna_df2.shape[0]):
    y=len(lncrna_df2.iloc[x]["Sequence"])
    if(y>total):
        total=y
print(total)
    
print(str(total/lncrna_df2.shape[0]))

In [5]:
#divide data into a holdout set and training test set, hardcoded at 80/20 split
def partition_data(df):
    
    train_size = int(len(df)*0.80)
    ho_size = int(len(df)) - train_size
    
    train_df = df.sample(train_size)
    ho_df = df.drop(train_df.index)
    #final column of what it was set to 
    train_df['set'] = 'train'
    ho_df['set'] = 'holdout'
    
    return train_df, ho_df

In [6]:
#split data into training and holdout
#train_mrna_df, ho_mrna_df = partition_data(mrna_df)
train_lncrna_df, ho_lncrna_df = partition_data(lncrna_df1)
#train_lncrna_df2, ho_lncrna_df2 = partition_data(lncrna_df2)
train_random_df1, ho_random_df1 = partition_data(random_df1)
#train_random_df2, ho_random_df2 = partition_data(random_df2)

In [7]:
#concat all training data together and holdout data together
train_test_df = pd.concat([train_lncrna_df, train_random_df1], axis = 0, ignore_index = True)
holdout_df = pd.concat([ho_lncrna_df, ho_random_df1], axis = 0, ignore_index = True)

In [8]:
#drop set column
train_test_df.drop("set", axis = 1, inplace = True)
holdout_df.drop("set", axis = 1, inplace = True)

forbidden_strings = ['N', 'Y', 'D', 'S', 'K', 'W', 'M', 'R', 'V', 'H', 'B']

#check shape before removal
print(train_test_df.shape)
print(holdout_df.shape)

#Remove any rows with forbidden strings in sequence by equalling rows that don't (~) have 'forbidden string' in sequence
for S in forbidden_strings:
    train_test_df = train_test_df[~train_test_df.Sequence.map(lambda x: S in x.upper())]
    holdout_df = holdout_df[~holdout_df.Sequence.map(lambda x: S in x.upper())]

#check shape after removal
print(train_test_df.shape)
print(holdout_df.shape)

(6592, 2)
(1649, 2)
(6585, 2)
(1648, 2)


In [9]:
#shuffle
train_test_df = train_test_df.sample(frac=1)
print(train_test_df)
holdout_df = holdout_df.sample(frac=1)
print(holdout_df)

#save to file
train_test_df.to_csv("train_test.csv", index=False)
holdout_df.to_csv("holdout.csv", index=False)

                                               Sequence      Target
5210  TGCAATTTTGGCAAAAAAAGGTAAAAACAAGATTACAATAATTTTG...  not_lncRNA
5277  ACATCTTGAGCAACTCCAGAATCCCTAGCACGATGTCGTTTACATA...  not_lncRNA
3327  CAGAGGATTAAAGTTGACACCCATGAAACATTCAGAGCTGCCGTAA...      lncRNA
1052  TCTAATTTTCTTGACGCTAGTCTTTCTTTCCGGAAACATCATCTTC...      lncRNA
3188  CGACTGAAAAATATCAAGGTAGAGAGACAAGGTCAATCAAATACAA...      lncRNA
...                                                 ...         ...
2659  TGAGTATTCCCAAACCACCTGGCTGAATAAGTAAGAGTTCCTTGGT...      lncRNA
1685  TTTTAAATCAAGAGCCCTCTCCCTCATGGCTGCACCTTCTTCATCT...      lncRNA
3130  CATCGATCTACGCCGTGTCCCGCCGCGGAAACCCGACGGAGATGAA...      lncRNA
5909  TTCAAGAACATAAGTATGATGGTCCCGTACCACAATAAGTTTTTGT...  not_lncRNA
4731  AAATATTTCATAAACAACAAAAGTGCGGAACTTATGCCTTTGGATT...  not_lncRNA

[6585 rows x 2 columns]
                                               Sequence      Target
397   AAAAGGGTTTTAATTATGTATTTATAAATGTAGAGAGGTACGTATA...      lncRNA
1640  CATTGATAGTGACTTAG

In [11]:
#Unccoment first time you run this cell
#!mv motif/motif_utils.py .
from motif_utils import *
import sys
def csv_to_dnabert_tsv(in_string, out_string, kmer):
    csv_file = in_string
    my_k = kmer
    df = pd.read_csv(csv_file)
    seq_array = []
    label_array = []
    for i, row in df.iterrows():
        seq = row["Sequence"]
        label = row["Target"]
        seq = seq2kmer(seq,my_k)
        seq_array.append(seq)
        if(label == "lncRNA"):
               label = 0
        else:
               label = 1
        label_array.append(label)
        print(label)
    data = np.array([seq_array, label_array])
    data = data.T
    print(data)
    new_df = pd.DataFrame(data, columns=["sequence", "label"], index=None)
    print(new_df)
    new_df.to_csv(out_string, sep="\t", header=True, index=False)

In [12]:
#Should now be in format that is DNABERT friendly, output has to be train.tsv and dev.tsv for DNABERT
#final arg is kmer size, adjust for which model you've downloaded from their pretrained
csv_to_dnabert_tsv("train_test.csv", "train.tsv", 3)
csv_to_dnabert_tsv("holdout.csv", "dev.tsv", 3)
!mv *.tsv input_data_3mer/
csv_to_dnabert_tsv("train_test.csv", "train.tsv", 4)
csv_to_dnabert_tsv("holdout.csv", "dev.tsv", 4)
!mv *.tsv input_data_4mer/
csv_to_dnabert_tsv("train_test.csv", "train.tsv", 5)
csv_to_dnabert_tsv("holdout.csv", "dev.tsv", 5)
!mv *.tsv input_data_5mer/
csv_to_dnabert_tsv("train_test.csv", "train.tsv", 6)
csv_to_dnabert_tsv("holdout.csv", "dev.tsv", 6)
!mv *.tsv input_data_6mer/

1
1
0
0
0
0
1
1
0
1
1
1
0
1
1
1
0
1
0
1
1
1
1
1
0
0
1
0
1
1
0
0
1
1
1
1
0
0
1
0
0
1
1
0
0
1
0
0
1
1
0
1
0
0
0
0
1
0
0
1
0
0
0
1
0
1
1
1
0
0
0
1
1
0
1
1
0
1
0
0
1
1
0
1
1
0
1
1
1
0
1
0
0
0
1
0
1
1
0
1
1
0
0
1
1
0
0
0
0
1
1
1
1
1
1
0
1
0
0
1
1
0
1
1
1
0
1
0
0
1
1
1
1
1
0
0
0
0
0
1
1
1
0
1
1
1
0
0
1
1
1
1
0
0
0
1
1
1
1
1
0
0
1
0
0
1
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
1
1
0
1
0
0
1
1
0
1
1
1
0
0
0
0
1
1
0
1
1
1
0
0
1
1
0
0
1
0
0
1
0
1
1
0
1
1
1
0
0
0
0
0
1
0
1
1
1
0
1
1
0
1
1
1
0
0
1
0
0
1
0
1
1
0
1
0
0
1
1
1
0
0
0
0
0
1
1
1
0
1
0
1
0
1
1
1
0
1
0
1
1
1
0
1
0
1
1
1
0
0
0
0
0
1
0
1
1
0
0
0
1
0
0
1
0
1
0
1
1
1
1
0
0
0
0
0
0
0
1
0
0
0
0
0
1
0
1
1
0
0
0
1
0
0
0
0
1
0
1
1
1
1
0
1
1
0
0
1
0
0
0
1
1
0
0
0
0
1
0
1
1
1
0
0
0
1
0
1
0
1
0
0
1
1
0
0
0
0
0
0
0
0
1
0
0
0
0
1
1
0
0
1
1
0
1
1
1
1
1
0
0
1
1
1
0
1
1
1
0
1
0
1
0
1
0
0
0
0
1
1
0
0
1
1
1
0
0
1
0
0
0
0
0
1
1
1
1
1
1
0
1
1
0
0
0
0
0
0
1
1
0
1
1
0
0
0
1
1
1
0
1
0
0
0
1
0
0
1
1
1
1
0
1
0
0
1
1
0
1
0
1
1
0
1
0
0
0
1
0
1
0
0
0
0
1
0
0
1
1
1
0
0
1
1
0
1
1


1
1
0
0
1
1
1
1
1
0
0
0
1
0
0
0
1
0
0
0
1
1
0
1
1
1
0
1
0
0
0
0
0
0
0
1
0
1
0
1
0
1
1
1
0
0
1
0
0
1
1
1
1
0
0
1
1
0
0
1
1
0
0
0
1
0
0
0
1
0
0
0
1
1
0
0
0
1
0
0
0
0
1
0
0
1
0
0
0
0
0
0
0
1
0
1
1
1
0
0
1
0
1
1
0
0
0
0
0
0
1
0
0
1
1
0
1
0
1
1
1
1
1
0
0
1
1
0
1
0
0
1
1
1
1
1
1
1
0
0
0
0
0
1
1
1
0
1
0
1
1
0
1
0
1
0
0
1
1
0
1
1
1
0
0
0
0
1
1
0
1
0
1
0
0
0
0
0
1
0
0
0
1
0
1
0
0
0
1
0
0
1
0
0
0
0
1
1
0
1
1
0
1
0
1
1
1
1
0
0
0
0
1
1
0
0
1
0
1
1
1
1
0
1
1
0
0
1
0
1
0
1
0
0
0
1
1
0
0
1
0
0
1
0
0
1
1
1
0
0
1
0
1
1
1
1
0
0
0
0
0
0
0
0
1
1
0
0
0
1
1
0
1
1
0
0
0
1
1
0
1
1
1
1
0
0
0
1
0
0
1
1
1
0
0
1
0
0
0
1
0
0
0
0
0
1
1
0
0
0
0
1
0
1
1
1
1
0
0
1
0
0
1
0
1
0
0
1
0
1
1
0
0
0
0
1
1
1
0
1
1
0
0
0
0
1
0
0
0
0
0
0
1
1
0
0
0
1
1
1
1
1
0
0
0
1
0
1
0
1
0
0
0
1
0
0
0
1
1
0
0
1
1
0
0
0
0
1
0
0
1
0
0
0
1
0
1
1
1
1
1
1
1
0
1
0
1
0
0
1
1
1
1
1
1
0
1
0
0
1
0
1
0
0
0
0
0
0
1
0
0
0
1
0
1
0
1
0
0
1
1
1
1
0
0
1
1
1
1
1
0
0
1
0
0
1
0
0
1
1
1
1
1
1
0
1
0
0
1
0
1
0
0
1
0
0
0
0
0
0
0
0
0
1
1
0
0
1
0
1
1
0
0
1
1
0
0
0
1
1


0
1
0
1
1
0
0
0
1
0
1
1
0
0
0
0
1
0
0
0
0
0
1
1
1
0
0
1
1
1
1
0
0
0
1
1
1
1
1
1
1
0
0
0
1
0
0
1
0
1
1
1
1
1
0
0
0
1
0
1
0
1
1
1
0
0
1
1
1
1
1
1
1
1
0
1
0
0
0
1
1
1
0
1
0
0
1
0
0
0
0
1
0
0
0
0
0
0
1
1
1
1
0
0
1
1
1
0
1
0
0
0
1
1
1
0
1
1
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
1
0
1
1
1
1
1
0
1
1
1
0
0
0
1
1
0
1
0
1
0
1
1
1
1
0
1
0
0
1
1
1
1
1
0
0
0
1
0
0
0
1
1
0
0
0
0
1
1
1
0
0
1
1
0
0
1
1
0
0
1
0
0
0
1
1
1
1
0
0
0
0
1
1
0
0
1
1
1
0
0
0
1
0
0
0
1
0
1
0
1
0
1
1
0
1
0
0
1
0
1
1
1
0
0
1
1
0
1
0
0
1
0
1
1
1
0
0
1
0
0
1
1
1
0
0
1
1
0
0
0
1
0
0
1
1
1
1
0
0
1
0
1
0
1
1
0
1
1
1
0
1
1
1
0
0
1
1
1
1
0
0
1
1
1
0
1
1
0
1
1
0
1
1
1
1
0
1
0
0
0
1
1
0
1
0
0
1
0
1
1
0
0
0
0
0
0
0
1
0
1
1
1
0
0
0
0
0
1
0
0
1
0
1
1
0
0
0
0
0
1
0
0
0
0
1
0
0
0
1
1
1
0
1
0
0
1
1
1
1
1
1
1
1
1
0
0
1
1
0
0
1
1
0
0
1
1
1
1
0
1
1
1
1
0
0
0
0
1
0
0
1
0
0
1
0
0
0
1
1
0
1
1
0
1
0
0
0
1
1
1
0
1
1
0
0
0
1
1
0
0
0
1
1
1
1
1
1
1
1
0
0
0
0
0
0
0
1
0
0
1
0
1
1
1
1
0
0
1
0
1
1
0
1
0
1
1
0
1
1
0
0
0
0
0
0
1
0
0
1
0
0
1
0
1
0
0
0
1
0
0
1
0
1
1
1
1


1
1
0
0
0
0
1
1
0
1
1
1
0
1
1
1
0
1
0
1
1
1
1
1
0
0
1
0
1
1
0
0
1
1
1
1
0
0
1
0
0
1
1
0
0
1
0
0
1
1
0
1
0
0
0
0
1
0
0
1
0
0
0
1
0
1
1
1
0
0
0
1
1
0
1
1
0
1
0
0
1
1
0
1
1
0
1
1
1
0
1
0
0
0
1
0
1
1
0
1
1
0
0
1
1
0
0
0
0
1
1
1
1
1
1
0
1
0
0
1
1
0
1
1
1
0
1
0
0
1
1
1
1
1
0
0
0
0
0
1
1
1
0
1
1
1
0
0
1
1
1
1
0
0
0
1
1
1
1
1
0
0
1
0
0
1
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
1
1
0
1
0
0
1
1
0
1
1
1
0
0
0
0
1
1
0
1
1
1
0
0
1
1
0
0
1
0
0
1
0
1
1
0
1
1
1
0
0
0
0
0
1
0
1
1
1
0
1
1
0
1
1
1
0
0
1
0
0
1
0
1
1
0
1
0
0
1
1
1
0
0
0
0
0
1
1
1
0
1
0
1
0
1
1
1
0
1
0
1
1
1
0
1
0
1
1
1
0
0
0
0
0
1
0
1
1
0
0
0
1
0
0
1
0
1
0
1
1
1
1
0
0
0
0
0
0
0
1
0
0
0
0
0
1
0
1
1
0
0
0
1
0
0
0
0
1
0
1
1
1
1
0
1
1
0
0
1
0
0
0
1
1
0
0
0
0
1
0
1
1
1
0
0
0
1
0
1
0
1
0
0
1
1
0
0
0
0
0
0
0
0
1
0
0
0
0
1
1
0
0
1
1
0
1
1
1
1
1
0
0
1
1
1
0
1
1
1
0
1
0
1
0
1
0
0
0
0
1
1
0
0
1
1
1
0
0
1
0
0
0
0
0
1
1
1
1
1
1
0
1
1
0
0
0
0
0
0
1
1
0
1
1
0
0
0
1
1
1
0
1
0
0
0
1
0
0
1
1
1
1
0
1
0
0
1
1
0
1
0
1
1
0
1
0
0
0
1
0
1
0
0
0
0
1
0
0
1
1
1
0
0
1
1
0
1
1


1
0
1
0
1
0
1
1
0
1
1
0
1
1
0
1
1
1
1
0
1
0
1
1
0
1
0
1
1
0
1
0
0
1
1
0
0
1
1
1
1
1
0
1
1
1
1
1
1
0
1
1
0
0
1
0
0
0
1
0
0
1
1
0
0
0
1
1
1
1
0
0
1
1
0
1
1
0
0
1
1
1
1
1
0
0
0
1
0
0
0
1
0
0
0
1
1
0
1
1
1
0
1
0
0
0
0
0
0
0
1
0
1
0
1
0
1
1
1
0
0
1
0
0
1
1
1
1
0
0
1
1
0
0
1
1
0
0
0
1
0
0
0
1
0
0
0
1
1
0
0
0
1
0
0
0
0
1
0
0
1
0
0
0
0
0
0
0
1
0
1
1
1
0
0
1
0
1
1
0
0
0
0
0
0
1
0
0
1
1
0
1
0
1
1
1
1
1
0
0
1
1
0
1
0
0
1
1
1
1
1
1
1
0
0
0
0
0
1
1
1
0
1
0
1
1
0
1
0
1
0
0
1
1
0
1
1
1
0
0
0
0
1
1
0
1
0
1
0
0
0
0
0
1
0
0
0
1
0
1
0
0
0
1
0
0
1
0
0
0
0
1
1
0
1
1
0
1
0
1
1
1
1
0
0
0
0
1
1
0
0
1
0
1
1
1
1
0
1
1
0
0
1
0
1
0
1
0
0
0
1
1
0
0
1
0
0
1
0
0
1
1
1
0
0
1
0
1
1
1
1
0
0
0
0
0
0
0
0
1
1
0
0
0
1
1
0
1
1
0
0
0
1
1
0
1
1
1
1
0
0
0
1
0
0
1
1
1
0
0
1
0
0
0
1
0
0
0
0
0
1
1
0
0
0
0
1
0
1
1
1
1
0
0
1
0
0
1
0
1
0
0
1
0
1
1
0
0
0
0
1
1
1
0
1
1
0
0
0
0
1
0
0
0
0
0
0
1
1
0
0
0
1
1
1
1
1
0
0
0
1
0
1
0
1
0
0
0
1
0
0
0
1
1
0
0
1
1
0
0
0
0
1
0
0
1
0
0
0
1
0
1
1
1
1
1
1
1
0
1
0
1
0
0
1
1
1
1
1
1
0
1
0
0
1
0
1
0
0
0


...

0
1
0
1
1
0
0
0
1
0
1
1
0
0
0
0
1
0
0
0
0
0
1
1
1
0
0
1
1
1
1
0
0
0
1
1
1
1
1
1
1
0
0
0
1
0
0
1
0
1
1
1
1
1
0
0
0
1
0
1
0
1
1
1
0
0
1
1
1
1
1
1
1
1
0
1
0
0
0
1
1
1
0
1
0
0
1
0
0
0
0
1
0
0
0
0
0
0
1
1
1
1
0
0
1
1
1
0
1
0
0
0
1
1
1
0
1
1
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
1
0
1
1
1
1
1
0
1
1
1
0
0
0
1
1
0
1
0
1
0
1
1
1
1
0
1
0
0
1
1
1
1
1
0
0
0
1
0
0
0
1
1
0
0
0
0
1
1
1
0
0
1
1
0
0
1
1
0
0
1
0
0
0
1
1
1
1
0
0
0
0
1
1
0
0
1
1
1
0
0
0
1
0
0
0
1
0
1
0
1
0
1
1
0
1
0
0
1
0
1
1
1
0
0
1
1
0
1
0
0
1
0
1
1
1
0
0
1
0
0
1
1
1
0
0
1
1
0
0
0
1
0
0
1
1
1
1
0
0
1
0
1
0
1
1
0
1
1
1
0
1
1
1
0
0
1
1
1
1
0
0
1
1
1
0
1
1
0
1
1
0
1
1
1
1
0
1
0
0
0
1
1
0
1
0
0
1
0
1
1
0
0
0
0
0
0
0
1
0
1
1
1
0
0
0
0
0
1
0
0
1
0
1
1
0
0
0
0
0
1
0
0
0
0
1
0
0
0
1
1
1
0
1
0
0
1
1
1
1
1
1
1
1
1
0
0
1
1
0
0
1
1
0
0
1
1
1
1
0
1
1
1
1
0
0
0
0
1
0
0
1
0
0
1
0
0
0
1
1
0
1
1
0
1
0
0
0
1
1
1
0
1
1
0
0
0
1
1
0
0
0
1
1
1
1
1
1
1
1
0
0
0
0
0
0
0
1
0
0
1
0
1
1
1
1
0
0
1
0
1
1
0
1
0
1
1
0
1
1
0
0
0
0
0
0
1
0
0
1
0
0
1
0
1
0
0
0
1
0
0
1
0
1
1
1
1


1
1
0
0
0
0
1
1
0
1
1
1
0
1
1
1
0
1
0
1
1
1
1
1
0
0
1
0
1
1
0
0
1
1
1
1
0
0
1
0
0
1
1
0
0
1
0
0
1
1
0
1
0
0
0
0
1
0
0
1
0
0
0
1
0
1
1
1
0
0
0
1
1
0
1
1
0
1
0
0
1
1
0
1
1
0
1
1
1
0
1
0
0
0
1
0
1
1
0
1
1
0
0
1
1
0
0
0
0
1
1
1
1
1
1
0
1
0
0
1
1
0
1
1
1
0
1
0
0
1
1
1
1
1
0
0
0
0
0
1
1
1
0
1
1
1
0
0
1
1
1
1
0
0
0
1
1
1
1
1
0
0
1
0
0
1
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
1
1
0
1
0
0
1
1
0
1
1
1
0
0
0
0
1
1
0
1
1
1
0
0
1
1
0
0
1
0
0
1
0
1
1
0
1
1
1
0
0
0
0
0
1
0
1
1
1
0
1
1
0
1
1
1
0
0
1
0
0
1
0
1
1
0
1
0
0
1
1
1
0
0
0
0
0
1
1
1
0
1
0
1
0
1
1
1
0
1
0
1
1
1
0
1
0
1
1
1
0
0
0
0
0
1
0
1
1
0
0
0
1
0
0
1
0
1
0
1
1
1
1
0
0
0
0
0
0
0
1
0
0
0
0
0
1
0
1
1
0
0
0
1
0
0
0
0
1
0
1
1
1
1
0
1
1
0
0
1
0
0
0
1
1
0
0
0
0
1
0
1
1
1
0
0
0
1
0
1
0
1
0
0
1
1
0
0
0
0
0
0
0
0
1
0
0
0
0
1
1
0
0
1
1
0
1
1
1
1
1
0
0
1
1
1
0
1
1
1
0
1
0
1
0
1
0
0
0
0
1
1
0
0
1
1
1
0
0
1
0
0
0
0
0
1
1
1
1
1
1
0
1
1
0
0
0
0
0
0
1
1
0
1
1
0
0
0
1
1
1
0
1
0
0
0
1
0
0
1
1
1
1
0
1
0
0
1
1
0
1
0
1
1
0
1
0
0
0
1
0
1
0
0
0
0
1
0
0
1
1
1
0
0
1
1
0
1
1


0
1
1
1
0
0
0
0
1
0
1
0
0
0
1
0
0
0
1
0
0
0
1
0
0
1
0
1
1
0
0
1
0
1
1
0
0
1
0
0
0
0
0
1
0
0
1
0
0
1
0
1
0
1
1
0
0
1
0
0
0
0
0
1
0
0
1
1
1
1
0
0
0
1
1
0
1
0
0
1
0
1
0
0
0
1
0
0
0
1
1
0
0
0
1
0
1
1
0
0
1
1
1
0
1
1
1
0
1
1
1
1
0
0
1
1
0
0
1
0
0
1
1
0
1
0
0
1
1
0
0
0
1
1
0
0
0
0
0
1
1
0
0
0
0
0
1
1
0
0
0
0
1
0
1
0
1
1
1
0
1
1
0
1
0
1
0
1
0
0
0
0
0
0
1
0
1
1
0
1
0
1
1
1
1
0
0
0
1
0
1
0
0
0
1
0
0
0
0
0
1
1
0
0
0
1
0
0
1
1
1
0
1
1
1
0
1
0
1
0
0
1
1
1
1
0
0
0
1
1
1
0
0
0
1
0
0
1
1
0
0
1
1
1
1
1
0
0
0
0
1
1
1
1
1
0
0
0
0
1
0
1
1
1
1
0
0
1
0
0
1
1
0
0
0
0
0
1
0
0
1
0
0
0
1
1
0
0
0
0
0
1
1
0
1
1
0
1
1
0
1
0
0
1
1
1
0
1
1
1
1
0
1
1
1
0
0
1
0
1
1
0
1
0
1
1
0
1
0
0
1
0
1
0
1
1
0
0
1
1
0
0
1
0
1
0
0
0
1
1
0
1
0
1
0
1
0
0
0
1
0
0
1
0
1
1
0
1
1
0
1
0
0
1
1
0
0
0
1
1
1
0
0
1
1
0
0
1
1
0
0
0
0
0
1
1
1
1
0
1
0
1
0
1
0
1
1
1
1
0
0
0
1
1
1
1
1
1
0
0
0
1
1
1
0
0
1
1
1
0
1
0
1
0
1
1
0
1
1
0
1
1
0
1
1
1
1
0
1
0
1
1
0
1
0
1
1
0
1
0
0
1
1
0
0
1
1
1
1
1
0
1
1
1
1
1
1
0
1
1
0
0
1
0
0
0
1
0
0
1
1
0
0
0
1
1
1
1
0
0


0
1
0
1
1
0
0
0
1
0
1
1
0
0
0
0
1
0
0
0
0
0
1
1
1
0
0
1
1
1
1
0
0
0
1
1
1
1
1
1
1
0
0
0
1
0
0
1
0
1
1
1
1
1
0
0
0
1
0
1
0
1
1
1
0
0
1
1
1
1
1
1
1
1
0
1
0
0
0
1
1
1
0
1
0
0
1
0
0
0
0
1
0
0
0
0
0
0
1
1
1
1
0
0
1
1
1
0
1
0
0
0
1
1
1
0
1
1
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
1
0
1
1
1
1
1
0
1
1
1
0
0
0
1
1
0
1
0
1
0
1
1
1
1
0
1
0
0
1
1
1
1
1
0
0
0
1
0
0
0
1
1
0
0
0
0
1
1
1
0
0
1
1
0
0
1
1
0
0
1
0
0
0
1
1
1
1
0
0
0
0
1
1
0
0
1
1
1
0
0
0
1
0
0
0
1
0
1
0
1
0
1
1
0
1
0
0
1
0
1
1
1
0
0
1
1
0
1
0
0
1
0
1
1
1
0
0
1
0
0
1
1
1
0
0
1
1
0
0
0
1
0
0
1
1
1
1
0
0
1
0
1
0
1
1
0
1
1
1
0
1
1
1
0
0
1
1
1
1
0
0
1
1
1
0
1
1
0
1
1
0
1
1
1
1
0
1
0
0
0
1
1
0
1
0
0
1
0
1
1
0
0
0
0
0
0
0
1
0
1
1
1
0
0
0
0
0
1
0
0
1
0
1
1
0
0
0
0
0
1
0
0
0
0
1
0
0
0
1
1
1
0
1
0
0
1
1
1
1
1
1
1
1
1
0
0
1
1
0
0
1
1
0
0
1
1
1
1
0
1
1
1
1
0
0
0
0
1
0
0
1
0
0
1
0
0
0
1
1
0
1
1
0
1
0
0
0
1
1
1
0
1
1
0
0
0
1
1
0
0
0
1
1
1
1
1
1
1
1
0
0
0
0
0
0
0
1
0
0
1
0
1
1
1
1
0
0
1
0
1
1
0
1
0
1
1
0
1
1
0
0
0
0
0
0
1
0
0
1
0
0
1
0
1
0
0
0
1
0
0
1
0
1
1
1
1


                                               sequence label
0     AAAAGG AAAGGG AAGGGT AGGGTT GGGTTT GGTTTT GTTT...     0
1     CATTGA ATTGAT TTGATA TGATAG GATAGT ATAGTG TAGT...     1
2     CCCTCC CCTCCC CTCCCA TCCCAT CCCATA CCATAT CATA...     0
3     CTCAAA TCAAAA CAAAAA AAAAAT AAAATT AAATTA AATT...     1
4     GAACCA AACCAT ACCATC CCATCA CATCAG ATCAGA TCAG...     1
...                                                 ...   ...
1643  CAGATA AGATAA GATAAC ATAACT TAACTA AACTAT ACTA...     1
1644  CTCTGT TCTGTG CTGTGG TGTGGT GTGGTG TGGTGC GGTG...     0
1645  GTTTTC TTTTCC TTTCCT TTCCTT TCCTTG CCTTGT CTTG...     0
1646  TATCTT ATCTTG TCTTGC CTTGCA TTGCAA TGCAAC GCAA...     1
1647  TCCAAA CCAAAT CAAATC AAATCA AATCAT ATCATG TCAT...     1

[1648 rows x 2 columns]


# Fine Tune Models with Arabidopsis Data

## 3mer

In [13]:
#hardocded the variables, not sure how to do this with env variables above :(
#!mv examples/run_finetune.py .
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna3 \
    --model_name_or_path=/group/pawsey0149/mgill/dl_playground/DNABERT_aT/3-new-12w-0/ \
    --task_name dnaprom \
    --do_train \
    --do_eval \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_3mer \
    --max_seq_length 2048 \
    --per_gpu_eval_batch_size=4   \
    --per_gpu_train_batch_size=4   \
    --learning_rate 2e-5 \
    --num_train_epochs 4.0 \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/ \
    --evaluate_during_training \
    --logging_steps 100 \
    --save_steps 4000 \
    --warmup_percent 0.1 \
    --hidden_dropout_prob 0.1 \
    --overwrite_output \
    --weight_decay 0.01 \
    --n_process 8

05/25/2021 13:51:39 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
05/25/2021 13:51:39 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/3-new-12w-0/config.json
05/25/2021 13:51:39 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1
  },
  "layer_norm_eps": 1e-12,
  "length_penalty": 1.0,
  "max_length": 20,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attentio

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 13:51:39 - INFO - transformers.tokenization_utils -   loading file https://raw.githubusercontent.com/jerryji1993/DNABERT/master/src/transformers/dnabert-config/bert-config-3/vocab.txt from cache at /home/mgill/.cache/torch/transformers/e1e7221d086d0af09215b2c6ef3ded41de274c79ace1930c48dfce242a7b36fa.b24b7bce4d95258cccdbc46b651c8283db3a0f1324fb97567c8b22b19970f82c
05/25/2021 13:51:39 - INFO - transformers.modeling_utils -   loading weights file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/3-new-12w-0/pytorch_model.bin
05/25/2021 13:51:41 - INFO - transformers.modeling_utils -   Weights of BertForLongSequenceClassificationCat not initialized from pretrained model: ['classifier1.weight', 'classifier1.bias', 'classifier2.weight', 'classifier2.bias']
05/25/2021 13:51:41 - INFO - transformers.modeling_utils -   Weights from pretrained model not used in BertForLongSequenceClassificationCat: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.tran

Iteration:  25%|██▌       | 99/390 [01:32<04:12,  1.15it/s]05/25/2021 13:53:20 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_3mer/cached_dev_3-new-12w-0_2048_dnaprom
05/25/2021 13:53:20 - INFO - __main__ -   ***** Running evaluation  *****
05/25/2021 13:53:20 - INFO - __main__ -     Num examples = 1557
05/25/2021 13:53:20 - INFO - __main__ -     Batch size = 16


Evaluating:   0%|          | 0/98 [00:00<?, ?it/s]

Evaluating:   1%|          | 1/98 [00:00<00:48,  2.02it/s]

Evaluating:   2%|▏         | 2/98 [00:00<00:41,  2.33it/s]

Evaluating:   3%|▎         | 3/98 [00:01<00:36,  2.62it/s]

Evaluating:   4%|▍         | 4/98 [00:01<00:32,  2.87it/s]

Evaluating:   5%|▌         | 5/98 [00:01<00:30,  3.08it/s]

Evaluating:   6%|▌         | 6/98 [00:01<00:28,  3.24it/s]

Evaluating:   7%|▋         | 7/98 [00:02<00:27,  3.36it/s]

Evaluating:   8%|▊         | 8/98 [00:02<00:26,  3.46it/s]

Evaluating:   9%|▉         | 9/9

Evaluating:  85%|████████▍ | 83/98 [00:23<00:04,  3.62it/s]

Evaluating:  86%|████████▌ | 84/98 [00:23<00:03,  3.62it/s]

Evaluating:  87%|████████▋ | 85/98 [00:23<00:03,  3.62it/s]

Evaluating:  88%|████████▊ | 86/98 [00:24<00:03,  3.62it/s]

Evaluating:  89%|████████▉ | 87/98 [00:24<00:03,  3.62it/s]

Evaluating:  90%|████████▉ | 88/98 [00:24<00:02,  3.63it/s]

Evaluating:  91%|█████████ | 89/98 [00:24<00:02,  3.63it/s]

Evaluating:  92%|█████████▏| 90/98 [00:25<00:02,  3.63it/s]

Evaluating:  93%|█████████▎| 91/98 [00:25<00:01,  3.62it/s]

Evaluating:  94%|█████████▍| 92/98 [00:25<00:01,  3.62it/s]

Evaluating:  95%|█████████▍| 93/98 [00:26<00:01,  3.62it/s]

Evaluating:  96%|█████████▌| 94/98 [00:26<00:01,  3.62it/s]

Evaluating:  97%|█████████▋| 95/98 [00:26<00:00,  3.62it/s]

Evaluating:  98%|█████████▊| 96/98 [00:26<00:00,  3.62it/s]

Evaluating:  99%|█████████▉| 97/98 [00:27<00:00,  3.62it/s]

Evaluating: 100%|██████████| 98/98 [00:27<00:00,  3.57it/s]
05/25/2021 13:53:48 - INF

...

{"eval_acc": 0.6936416184971098, "eval_f1": 0.6896764389185857, "eval_mcc": 0.39736734063200085, "eval_auc": 0.7579571066986546, "eval_precision": 0.703933164366845, "eval_recall": 0.693569304790599, "learning_rate": 8.547008547008548e-07, "loss": 0.49479113399982455, "step": 1500}


/home/mgill/.local/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:61: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '

Epoch: 100%|██████████| 4/4 [29:20<00:00, 440.05s/it]
05/25/2021 14:21:06 - INFO - __main__ -    global_step = 1560, average loss = 0.5702446857132972
05/25/2021 14:21:06 - INFO - __main__ -   Saving model checkpoint to /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/
05/25/2021 14:21:06 - INFO - transformers.configuration_utils -   Configuration saved in /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/config.json
05/25/2021 14:21:07 - INFO - transformers.modeling_utils -   Model weights saved in /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/pytorch_model.bin
05/25/2021 14:21:07 - INFO - transformers.configuration_utils -   loading configuration file /gr

05/25/2021 14:21:10 - INFO - transformers.tokenization_utils -   loading file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/special_tokens_map.json
05/25/2021 14:21:10 - INFO - transformers.tokenization_utils -   loading file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/tokenizer_config.json
05/25/2021 14:21:10 - INFO - __main__ -   Evaluate the following checkpoints: ['/group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/']
05/25/2021 14:21:10 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/config.json
05/25/2021 14:21:10 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForLongSequenceClassificationCat"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 

<class 'transformers.tokenization_dna.DNATokenizer'>
<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 14:21:12 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_3mer/cached_dev_3-new-12w-0_2048_dnaprom
05/25/2021 14:21:12 - INFO - __main__ -   ***** Running evaluation  *****
05/25/2021 14:21:12 - INFO - __main__ -     Num examples = 1557
05/25/2021 14:21:12 - INFO - __main__ -     Batch size = 16
Evaluating: 100%|██████████| 98/98 [00:26<00:00,  3.65it/s]
05/25/2021 14:21:39 - INFO - __main__ -   ***** Eval results  *****
05/25/2021 14:21:39 - INFO - __main__ -     acc = 0.6942838792549775
05/25/2021 14:21:39 - INFO - __main__ -     auc = 0.7589058545165346
05/25/2021 14:21:39 - INFO - __main__ -     f1 = 0.6911435239206534
05/25/2021 14:21:39 - INFO - __main__ -     mcc = 0.3965337349985078
05/25/2021 14:21:39 - INFO - __main__ -     precision = 0.7023986794366972
05/25/2021 14:21:39 - INFO - __main__ -     recall = 0.6942194032953724


In [14]:
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna3 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/ \
    --task_name dnaprom \
    --do_predict \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_3mer \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/results_3mer/

05/25/2021 14:21:40 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
05/25/2021 14:21:40 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/config.json
05/25/2021 14:21:40 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForLongSequenceClassificationCat"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1
  },
  "layer_norm_eps": 1e-12,
  "length_penalty": 1.0,
  "max_length": 20,
  "max_position_embeddings": 512,
  "model_type

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 14:21:40 - INFO - transformers.tokenization_utils -   loading file https://raw.githubusercontent.com/jerryji1993/DNABERT/master/src/transformers/dnabert-config/bert-config-3/vocab.txt from cache at /home/mgill/.cache/torch/transformers/e1e7221d086d0af09215b2c6ef3ded41de274c79ace1930c48dfce242a7b36fa.b24b7bce4d95258cccdbc46b651c8283db3a0f1324fb97567c8b22b19970f82c
05/25/2021 14:21:40 - INFO - transformers.modeling_utils -   loading weights file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_3mer/pytorch_model.bin
05/25/2021 14:21:42 - INFO - __main__ -   finish loading model
05/25/2021 14:21:42 - INFO - __main__ -   Training/evaluation parameters Namespace(adam_epsilon=1e-08, attention_probs_dropout_prob=0.1, beta1=0.9, beta2=0.999, cache_dir='', config_name='', data_dir='/group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_3mer', device=device(type='cuda'), do_ensemble_pred=False, do_eval=False, do_lower_case=False, do_predict=True, do_train=False, do_vi

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 14:21:44 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_3mer/cached_dev_2048_dnaprom
05/25/2021 14:21:44 - INFO - __main__ -   ***** Running prediction  *****
05/25/2021 14:21:44 - INFO - __main__ -     Num examples = 1557
05/25/2021 14:21:44 - INFO - __main__ -     Batch size = 32
Predicting:   0%|          | 0/49 [00:00<?, ?it/s]/home/mgill/.local/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:61: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
Predicting: 100%|██████████| 49/49 [00:24<00:00,  1.98it/s]
05/25/2021 14:22:09 - INFO - __main__ -   ***** Pred results  *****
05/25/2021 14:22:09 - INFO - __main__ -     acc = 0.6942838792549775
05/25/2021 14:22:09 - INFO - __main__ -     auc = 0.7589058545165346
05/25/2021 14:22:09 - INFO - __main__ - 

## 4mer

In [15]:
#hardocded the variables, not sure how to do this with env variables above :(
#!mv examples/run_finetune.py .
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna4 \
    --model_name_or_path=/group/pawsey0149/mgill/dl_playground/DNABERT_aT/4-new-12w-0/ \
    --task_name dnaprom \
    --do_train \
    --do_eval \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_4mer/ \
    --max_seq_length 2048 \
    --per_gpu_eval_batch_size=2   \
    --per_gpu_train_batch_size=2   \
    --learning_rate 2e-5 \
    --num_train_epochs 4.0 \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/ \
    --evaluate_during_training \
    --logging_steps 100 \
    --save_steps 4000 \
    --warmup_percent 0.1 \
    --hidden_dropout_prob 0.1 \
    --overwrite_output \
    --weight_decay 0.01 \
    --n_process 8

05/25/2021 14:22:09 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
05/25/2021 14:22:09 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/4-new-12w-0/config.json
05/25/2021 14:22:09 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1
  },
  "layer_norm_eps": 1e-12,
  "length_penalty": 1.0,
  "max_length": 20,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attentio

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 14:22:10 - INFO - transformers.tokenization_utils -   loading file https://raw.githubusercontent.com/jerryji1993/DNABERT/master/src/transformers/dnabert-config/bert-config-4/vocab.txt from cache at /home/mgill/.cache/torch/transformers/7e2907c40805f9ae104ef14f1bb0e1d375c6edddace059a06037bdc80e8abe91.29586c1860b95c4db60b7024d64161b951279c64e0d9eeea911f286be8f229ae
05/25/2021 14:22:10 - INFO - transformers.modeling_utils -   loading weights file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/4-new-12w-0/pytorch_model.bin
05/25/2021 14:22:12 - INFO - transformers.modeling_utils -   Weights of BertForLongSequenceClassificationCat not initialized from pretrained model: ['classifier1.weight', 'classifier1.bias', 'classifier2.weight', 'classifier2.bias']
05/25/2021 14:22:12 - INFO - transformers.modeling_utils -   Weights from pretrained model not used in BertForLongSequenceClassificationCat: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.tran

Iteration:  13%|█▎        | 99/779 [00:50<05:42,  1.98it/s]05/25/2021 14:23:05 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_4mer/cached_dev_4-new-12w-0_2048_dnaprom
05/25/2021 14:23:06 - INFO - __main__ -   ***** Running evaluation  *****
05/25/2021 14:23:06 - INFO - __main__ -     Num examples = 1557
05/25/2021 14:23:06 - INFO - __main__ -     Batch size = 8


Evaluating:   0%|          | 0/195 [00:00<?, ?it/s]

Evaluating:   1%|          | 1/195 [00:00<00:30,  6.32it/s]

Evaluating:   1%|          | 2/195 [00:00<00:30,  6.29it/s]

Evaluating:   2%|▏         | 3/195 [00:00<00:30,  6.25it/s]

Evaluating:   2%|▏         | 4/195 [00:00<00:30,  6.23it/s]

Evaluating:   3%|▎         | 5/195 [00:00<00:30,  6.21it/s]

Evaluating:   3%|▎         | 6/195 [00:00<00:30,  6.20it/s]

Evaluating:   4%|▎         | 7/195 [00:01<00:30,  6.20it/s]

Evaluating:   4%|▍         | 8/195 [00:01<00:30,  6.19it/s]

Evaluating:   5%|▍      

Evaluating:  42%|████▏     | 81/195 [00:13<00:18,  6.06it/s]

Evaluating:  42%|████▏     | 82/195 [00:13<00:18,  6.10it/s]

Evaluating:  43%|████▎     | 83/195 [00:13<00:18,  6.13it/s]

Evaluating:  43%|████▎     | 84/195 [00:13<00:18,  6.15it/s]

Evaluating:  44%|████▎     | 85/195 [00:14<00:17,  6.16it/s]

Evaluating:  44%|████▍     | 86/195 [00:14<00:17,  6.18it/s]

Evaluating:  45%|████▍     | 87/195 [00:14<00:17,  6.18it/s]

Evaluating:  45%|████▌     | 88/195 [00:14<00:17,  6.19it/s]

Evaluating:  46%|████▌     | 89/195 [00:14<00:17,  6.19it/s]

Evaluating:  46%|████▌     | 90/195 [00:14<00:16,  6.21it/s]

Evaluating:  47%|████▋     | 91/195 [00:14<00:16,  6.20it/s]

Evaluating:  47%|████▋     | 92/195 [00:15<00:16,  6.20it/s]

Evaluating:  48%|████▊     | 93/195 [00:15<00:16,  6.20it/s]

Evaluating:  48%|████▊     | 94/195 [00:15<00:16,  6.19it/s]

Evaluating:  49%|████▊     | 95/195 [00:15<00:16,  6.20it/s]

Evaluating:  49%|████▉     | 96/195 [00:15<00:15,  6.20it/s]

Evaluati

...

Evaluating:  72%|███████▏  | 141/195 [00:23<00:08,  6.20it/s]

Evaluating:  73%|███████▎  | 142/195 [00:23<00:08,  6.20it/s]

Evaluating:  73%|███████▎  | 143/195 [00:23<00:08,  6.20it/s]

Evaluating:  74%|███████▍  | 144/195 [00:23<00:08,  6.20it/s]

Evaluating:  74%|███████▍  | 145/195 [00:23<00:08,  6.20it/s]

Evaluating:  75%|███████▍  | 146/195 [00:24<00:07,  6.21it/s]

Evaluating:  75%|███████▌  | 147/195 [00:24<00:07,  6.20it/s]

Evaluating:  76%|███████▌  | 148/195 [00:24<00:07,  6.21it/s]

Evaluating:  76%|███████▋  | 149/195 [00:24<00:07,  6.21it/s]

Evaluating:  77%|███████▋  | 150/195 [00:24<00:07,  6.21it/s]

Evaluating:  77%|███████▋  | 151/195 [00:24<00:07,  6.21it/s]

Evaluating:  78%|███████▊  | 152/195 [00:24<00:06,  6.21it/s]

Evaluating:  78%|███████▊  | 153/195 [00:25<00:06,  6.21it/s]

Evaluating:  79%|███████▉  | 154/195 [00:25<00:06,  6.20it/s]

Evaluating:  79%|███████▉  | 155/195 [00:25<00:06,  6.20it/s]

Evaluating:  80%|████████  | 156/195 [00:25<00:06,  6.2

{"eval_acc": 0.6801541425818882, "eval_f1": 0.6777313942005566, "eval_mcc": 0.3656965513382588, "eval_auc": 0.7571766584936853, "eval_precision": 0.6856397923710653, "eval_recall": 0.6800987357729077, "learning_rate": 1.1408199643493762e-07, "loss": 0.5346015414595604, "step": 3100}



Epoch: 100%|██████████| 4/4 [43:13<00:00, 648.47s/it]
05/25/2021 15:05:28 - INFO - __main__ -    global_step = 3116, average loss = 0.5949764836804322
05/25/2021 15:05:28 - INFO - __main__ -   Saving model checkpoint to /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/
05/25/2021 15:05:28 - INFO - transformers.configuration_utils -   Configuration saved in /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/config.json
05/25/2021 15:05:30 - INFO - transformers.modeling_utils -   Model weights saved in /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/pytorch_model.bin
05/25/2021 15:05:30 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/config.json
05/25/2021 15:05:30 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForLongSequenceClassificationCat"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos

<class 'transformers.tokenization_dna.DNATokenizer'>
<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 15:05:34 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_4mer/cached_dev_4-new-12w-0_2048_dnaprom
05/25/2021 15:05:35 - INFO - __main__ -   ***** Running evaluation  *****
05/25/2021 15:05:35 - INFO - __main__ -     Num examples = 1557
05/25/2021 15:05:35 - INFO - __main__ -     Batch size = 8
Evaluating: 100%|██████████| 195/195 [00:32<00:00,  6.05it/s]
05/25/2021 15:06:07 - INFO - __main__ -   ***** Eval results  *****
05/25/2021 15:06:07 - INFO - __main__ -     acc = 0.6782273603082851
05/25/2021 15:06:07 - INFO - __main__ -     auc = 0.7571585085354302
05/25/2021 15:06:07 - INFO - __main__ -     f1 = 0.6756796198245056
05/25/2021 15:06:07 - INFO - __main__ -     mcc = 0.3620329463351601
05/25/2021 15:06:07 - INFO - __main__ -     precision = 0.6839076838182698
05/25/2021 15:06:07 - INFO - __main__ -     recall = 0.6781707152073551


In [16]:
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna4 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/ \
    --task_name dnaprom \
    --do_predict \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_4mer \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/results_4mer/

05/25/2021 15:06:07 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
05/25/2021 15:06:07 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/config.json
05/25/2021 15:06:07 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForLongSequenceClassificationCat"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1
  },
  "layer_norm_eps": 1e-12,
  "length_penalty": 1.0,
  "max_length": 20,
  "max_position_embeddings": 512,
  "model_type

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 15:06:08 - INFO - transformers.tokenization_utils -   loading file https://raw.githubusercontent.com/jerryji1993/DNABERT/master/src/transformers/dnabert-config/bert-config-4/vocab.txt from cache at /home/mgill/.cache/torch/transformers/7e2907c40805f9ae104ef14f1bb0e1d375c6edddace059a06037bdc80e8abe91.29586c1860b95c4db60b7024d64161b951279c64e0d9eeea911f286be8f229ae
05/25/2021 15:06:08 - INFO - transformers.modeling_utils -   loading weights file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_4mer/pytorch_model.bin
05/25/2021 15:06:10 - INFO - __main__ -   finish loading model
05/25/2021 15:06:10 - INFO - __main__ -   Training/evaluation parameters Namespace(adam_epsilon=1e-08, attention_probs_dropout_prob=0.1, beta1=0.9, beta2=0.999, cache_dir='', config_name='', data_dir='/group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_4mer', device=device(type='cuda'), do_ensemble_pred=False, do_eval=False, do_lower_case=False, do_predict=True, do_train=False, do_vi

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 15:06:13 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_4mer/cached_dev_2048_dnaprom
05/25/2021 15:06:13 - INFO - __main__ -   ***** Running prediction  *****
05/25/2021 15:06:13 - INFO - __main__ -     Num examples = 1557
05/25/2021 15:06:13 - INFO - __main__ -     Batch size = 32
Predicting:   0%|          | 0/49 [00:00<?, ?it/s]/home/mgill/.local/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:61: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
Predicting: 100%|██████████| 49/49 [00:24<00:00,  1.98it/s]
05/25/2021 15:06:38 - INFO - __main__ -   ***** Pred results  *****
05/25/2021 15:06:38 - INFO - __main__ -     acc = 0.6782273603082851
05/25/2021 15:06:38 - INFO - __main__ -     auc = 0.7571585085354302
05/25/2021 15:06:38 - INFO - __main__ - 

## 5mer

In [17]:
#hardocded the variables, not sure how to do this with env variables above :(
#!mv examples/run_finetune.py .
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna5 \
    --model_name_or_path=/group/pawsey0149/mgill/dl_playground/DNABERT_aT/5-new-12w-0/ \
    --task_name dnaprom \
    --do_train \
    --do_eval \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_5mer/ \
    --max_seq_length 2048 \
    --per_gpu_eval_batch_size=2   \
    --per_gpu_train_batch_size=2   \
    --learning_rate 2e-5 \
    --num_train_epochs 4.0 \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/ \
    --evaluate_during_training \
    --logging_steps 100 \
    --save_steps 4000 \
    --warmup_percent 0.1 \
    --hidden_dropout_prob 0.1 \
    --overwrite_output \
    --weight_decay 0.01 \
    --n_process 8

05/25/2021 15:06:38 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
05/25/2021 15:06:38 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/5-new-12w-0/config.json
05/25/2021 15:06:38 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1
  },
  "layer_norm_eps": 1e-12,
  "length_penalty": 1.0,
  "max_length": 20,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attentio

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 15:06:38 - INFO - transformers.tokenization_utils -   loading file https://raw.githubusercontent.com/jerryji1993/DNABERT/master/src/transformers/dnabert-config/bert-config-5/vocab.txt from cache at /home/mgill/.cache/torch/transformers/685498e46a419b3f23df06c611f1f3a88eac034537db33e2f77f448f55b84c64.222d8870b75e875fba4f058daa3d7be681c0401d3ea07303f4e0e646cfe28936
05/25/2021 15:06:38 - INFO - transformers.modeling_utils -   loading weights file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/5-new-12w-0/pytorch_model.bin
05/25/2021 15:06:41 - INFO - transformers.modeling_utils -   Weights of BertForLongSequenceClassificationCat not initialized from pretrained model: ['classifier1.weight', 'classifier1.bias', 'classifier2.weight', 'classifier2.bias']
05/25/2021 15:06:41 - INFO - transformers.modeling_utils -   Weights from pretrained model not used in BertForLongSequenceClassificationCat: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.tran

Iteration:  13%|█▎        | 99/779 [00:50<05:35,  2.03it/s]05/25/2021 15:07:34 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_5mer/cached_dev_5-new-12w-0_2048_dnaprom
05/25/2021 15:07:35 - INFO - __main__ -   ***** Running evaluation  *****
05/25/2021 15:07:35 - INFO - __main__ -     Num examples = 1557
05/25/2021 15:07:35 - INFO - __main__ -     Batch size = 8


Evaluating:   0%|          | 0/195 [00:00<?, ?it/s]

Evaluating:   1%|          | 1/195 [00:00<00:30,  6.35it/s]

Evaluating:   1%|          | 2/195 [00:00<00:30,  6.31it/s]

Evaluating:   2%|▏         | 3/195 [00:00<00:30,  6.28it/s]

Evaluating:   2%|▏         | 4/195 [00:00<00:30,  6.25it/s]

Evaluating:   3%|▎         | 5/195 [00:00<00:30,  6.24it/s]

Evaluating:   3%|▎         | 6/195 [00:00<00:30,  6.24it/s]

Evaluating:   4%|▎         | 7/195 [00:01<00:30,  6.22it/s]

Evaluating:   4%|▍         | 8/195 [00:01<00:30,  6.23it/s]

Evaluating:   5%|▍      

Evaluating:  42%|████▏     | 81/195 [00:13<00:18,  6.21it/s]

Evaluating:  42%|████▏     | 82/195 [00:13<00:18,  6.21it/s]

Evaluating:  43%|████▎     | 83/195 [00:13<00:18,  6.21it/s]

Evaluating:  43%|████▎     | 84/195 [00:13<00:17,  6.22it/s]

Evaluating:  44%|████▎     | 85/195 [00:13<00:17,  6.23it/s]

Evaluating:  44%|████▍     | 86/195 [00:14<00:17,  6.21it/s]

Evaluating:  45%|████▍     | 87/195 [00:14<00:17,  6.20it/s]

Evaluating:  45%|████▌     | 88/195 [00:14<00:17,  6.19it/s]

Evaluating:  46%|████▌     | 89/195 [00:14<00:17,  6.20it/s]

Evaluating:  46%|████▌     | 90/195 [00:14<00:16,  6.19it/s]

Evaluating:  47%|████▋     | 91/195 [00:14<00:16,  6.19it/s]

Evaluating:  47%|████▋     | 92/195 [00:15<00:20,  4.91it/s]

Evaluating:  48%|████▊     | 93/195 [00:15<00:19,  5.23it/s]

Evaluating:  48%|████▊     | 94/195 [00:15<00:18,  5.49it/s]

Evaluating:  49%|████▊     | 95/195 [00:15<00:17,  5.69it/s]

Evaluating:  49%|████▉     | 96/195 [00:15<00:17,  5.77it/s]

Evaluati

...

Evaluating:  72%|███████▏  | 141/195 [00:23<00:08,  6.20it/s]

Evaluating:  73%|███████▎  | 142/195 [00:23<00:08,  6.20it/s]

Evaluating:  73%|███████▎  | 143/195 [00:23<00:08,  6.21it/s]

Evaluating:  74%|███████▍  | 144/195 [00:23<00:08,  6.21it/s]

Evaluating:  74%|███████▍  | 145/195 [00:23<00:08,  6.21it/s]

Evaluating:  75%|███████▍  | 146/195 [00:23<00:07,  6.22it/s]

Evaluating:  75%|███████▌  | 147/195 [00:24<00:07,  6.21it/s]

Evaluating:  76%|███████▌  | 148/195 [00:24<00:07,  6.22it/s]

Evaluating:  76%|███████▋  | 149/195 [00:24<00:07,  6.21it/s]

Evaluating:  77%|███████▋  | 150/195 [00:24<00:07,  6.20it/s]

Evaluating:  77%|███████▋  | 151/195 [00:24<00:07,  6.20it/s]

Evaluating:  78%|███████▊  | 152/195 [00:24<00:06,  6.19it/s]

Evaluating:  78%|███████▊  | 153/195 [00:25<00:06,  6.13it/s]

Evaluating:  79%|███████▉  | 154/195 [00:25<00:06,  6.14it/s]

Evaluating:  79%|███████▉  | 155/195 [00:25<00:06,  6.15it/s]

Evaluating:  80%|████████  | 156/195 [00:25<00:06,  6.1

{"eval_acc": 0.6724470134874759, "eval_f1": 0.6720377792389305, "eval_mcc": 0.34569728996483945, "eval_auc": 0.7445426375519336, "eval_precision": 0.6732737293812553, "eval_recall": 0.672424603423412, "learning_rate": 1.1408199643493762e-07, "loss": 0.5467033597826958, "step": 3100}



Epoch: 100%|██████████| 4/4 [43:07<00:00, 646.87s/it]
05/25/2021 15:49:51 - INFO - __main__ -    global_step = 3116, average loss = 0.605045129959884
05/25/2021 15:49:51 - INFO - __main__ -   Saving model checkpoint to /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/
05/25/2021 15:49:51 - INFO - transformers.configuration_utils -   Configuration saved in /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/config.json
05/25/2021 15:49:52 - INFO - transformers.modeling_utils -   Model weights saved in /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/pytorch_model.bin
05/25/2021 15:49:52 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/config.json
05/25/2021 15:49:52 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForLongSequenceClassificationCat"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_

<class 'transformers.tokenization_dna.DNATokenizer'>
<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 15:49:56 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_5mer/cached_dev_5-new-12w-0_2048_dnaprom
05/25/2021 15:49:56 - INFO - __main__ -   ***** Running evaluation  *****
05/25/2021 15:49:56 - INFO - __main__ -     Num examples = 1557
05/25/2021 15:49:56 - INFO - __main__ -     Batch size = 8
Evaluating: 100%|██████████| 195/195 [00:32<00:00,  6.08it/s]
05/25/2021 15:50:28 - INFO - __main__ -   ***** Eval results  *****
05/25/2021 15:50:28 - INFO - __main__ -     acc = 0.6724470134874759
05/25/2021 15:50:28 - INFO - __main__ -     auc = 0.7445063376354235
05/25/2021 15:50:28 - INFO - __main__ -     f1 = 0.6719760010046398
05/25/2021 15:50:28 - INFO - __main__ -     mcc = 0.345823598536677
05/25/2021 15:50:28 - INFO - __main__ -     precision = 0.6734020310633214
05/25/2021 15:50:28 - INFO - __main__ -     recall = 0.672422953427207


In [18]:
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna5 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/ \
    --task_name dnaprom \
    --do_predict \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_5mer \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/results_5mer/

05/25/2021 15:50:28 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
05/25/2021 15:50:28 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/config.json
05/25/2021 15:50:28 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForLongSequenceClassificationCat"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1
  },
  "layer_norm_eps": 1e-12,
  "length_penalty": 1.0,
  "max_length": 20,
  "max_position_embeddings": 512,
  "model_type

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 15:50:29 - INFO - transformers.tokenization_utils -   loading file https://raw.githubusercontent.com/jerryji1993/DNABERT/master/src/transformers/dnabert-config/bert-config-5/vocab.txt from cache at /home/mgill/.cache/torch/transformers/685498e46a419b3f23df06c611f1f3a88eac034537db33e2f77f448f55b84c64.222d8870b75e875fba4f058daa3d7be681c0401d3ea07303f4e0e646cfe28936
05/25/2021 15:50:29 - INFO - transformers.modeling_utils -   loading weights file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_5mer/pytorch_model.bin
05/25/2021 15:50:31 - INFO - __main__ -   finish loading model
05/25/2021 15:50:31 - INFO - __main__ -   Training/evaluation parameters Namespace(adam_epsilon=1e-08, attention_probs_dropout_prob=0.1, beta1=0.9, beta2=0.999, cache_dir='', config_name='', data_dir='/group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_5mer', device=device(type='cuda'), do_ensemble_pred=False, do_eval=False, do_lower_case=False, do_predict=True, do_train=False, do_vi

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 15:50:33 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_5mer/cached_dev_2048_dnaprom
05/25/2021 15:50:33 - INFO - __main__ -   ***** Running prediction  *****
05/25/2021 15:50:33 - INFO - __main__ -     Num examples = 1557
05/25/2021 15:50:33 - INFO - __main__ -     Batch size = 32
Predicting:   0%|          | 0/49 [00:00<?, ?it/s]/home/mgill/.local/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:61: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
Predicting: 100%|██████████| 49/49 [00:24<00:00,  1.99it/s]
05/25/2021 15:50:58 - INFO - __main__ -   ***** Pred results  *****
05/25/2021 15:50:58 - INFO - __main__ -     acc = 0.6724470134874759
05/25/2021 15:50:58 - INFO - __main__ -     auc = 0.7445063376354235
05/25/2021 15:50:58 - INFO - __main__ - 

## 6mer

In [19]:
#hardocded the variables, not sure how to do this with env variables above :(
#!mv examples/run_finetune.py .
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna6 \
    --model_name_or_path=/group/pawsey0149/mgill/dl_playground/DNABERT_aT/6-new-12w-0/ \
    --task_name dnaprom \
    --do_train \
    --do_eval \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_6mer/ \
    --max_seq_length 2048 \
    --per_gpu_eval_batch_size=2   \
    --per_gpu_train_batch_size=2   \
    --learning_rate 2e-5 \
    --num_train_epochs 4.0 \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/ \
    --evaluate_during_training \
    --logging_steps 100 \
    --save_steps 4000 \
    --warmup_percent 0.1 \
    --hidden_dropout_prob 0.1 \
    --overwrite_output \
    --weight_decay 0.01 \
    --n_process 8

05/25/2021 15:50:58 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
05/25/2021 15:50:58 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/6-new-12w-0/config.json
05/25/2021 15:50:58 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1
  },
  "layer_norm_eps": 1e-12,
  "length_penalty": 1.0,
  "max_length": 20,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attentio

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 15:50:59 - INFO - transformers.tokenization_utils -   loading file https://raw.githubusercontent.com/jerryji1993/DNABERT/master/src/transformers/dnabert-config/bert-config-6/vocab.txt from cache at /home/mgill/.cache/torch/transformers/ea1474aad40c1c8ed4e1cb7c11345ddda6df27a857fb29e1d4c901d9b900d32d.26f8bd5a32e49c2a8271a46950754a4a767726709b7741c68723bc1db840a87e
05/25/2021 15:50:59 - INFO - transformers.modeling_utils -   loading weights file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/6-new-12w-0/pytorch_model.bin
05/25/2021 15:51:01 - INFO - transformers.modeling_utils -   Weights of BertForLongSequenceClassificationCat not initialized from pretrained model: ['classifier1.weight', 'classifier1.bias', 'classifier2.weight', 'classifier2.bias']
05/25/2021 15:51:01 - INFO - transformers.modeling_utils -   Weights from pretrained model not used in BertForLongSequenceClassificationCat: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.tran

Iteration:  13%|█▎        | 99/779 [00:50<05:46,  1.96it/s]05/25/2021 15:51:54 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_6mer/cached_dev_6-new-12w-0_2048_dnaprom
05/25/2021 15:51:54 - INFO - __main__ -   ***** Running evaluation  *****
05/25/2021 15:51:54 - INFO - __main__ -     Num examples = 1557
05/25/2021 15:51:54 - INFO - __main__ -     Batch size = 8


Evaluating:   0%|          | 0/195 [00:00<?, ?it/s]

Evaluating:   1%|          | 1/195 [00:00<00:31,  6.15it/s]

Evaluating:   1%|          | 2/195 [00:00<00:31,  6.18it/s]

Evaluating:   2%|▏         | 3/195 [00:00<00:31,  6.19it/s]

Evaluating:   2%|▏         | 4/195 [00:00<00:30,  6.19it/s]

Evaluating:   3%|▎         | 5/195 [00:00<00:30,  6.19it/s]

Evaluating:   3%|▎         | 6/195 [00:00<00:30,  6.19it/s]

Evaluating:   4%|▎         | 7/195 [00:01<00:30,  6.20it/s]

Evaluating:   4%|▍         | 8/195 [00:01<00:30,  6.18it/s]

Evaluating:   5%|▍      

Evaluating:  42%|████▏     | 81/195 [00:13<00:18,  6.18it/s]

Evaluating:  42%|████▏     | 82/195 [00:13<00:18,  6.19it/s]

Evaluating:  43%|████▎     | 83/195 [00:13<00:18,  6.19it/s]

Evaluating:  43%|████▎     | 84/195 [00:13<00:17,  6.19it/s]

Evaluating:  44%|████▎     | 85/195 [00:13<00:17,  6.20it/s]

Evaluating:  44%|████▍     | 86/195 [00:14<00:17,  6.20it/s]

Evaluating:  45%|████▍     | 87/195 [00:14<00:17,  6.19it/s]

Evaluating:  45%|████▌     | 88/195 [00:14<00:17,  6.19it/s]

Evaluating:  46%|████▌     | 89/195 [00:14<00:17,  6.19it/s]

Evaluating:  46%|████▌     | 90/195 [00:14<00:16,  6.18it/s]

Evaluating:  47%|████▋     | 91/195 [00:14<00:16,  6.18it/s]

Evaluating:  47%|████▋     | 92/195 [00:14<00:16,  6.18it/s]

Evaluating:  48%|████▊     | 93/195 [00:15<00:16,  6.19it/s]

Evaluating:  48%|████▊     | 94/195 [00:15<00:16,  6.19it/s]

Evaluating:  49%|████▊     | 95/195 [00:15<00:16,  6.20it/s]

Evaluating:  49%|████▉     | 96/195 [00:15<00:15,  6.20it/s]

Evaluati

...

Evaluating:  72%|███████▏  | 141/195 [00:23<00:08,  6.19it/s]

Evaluating:  73%|███████▎  | 142/195 [00:23<00:08,  6.19it/s]

Evaluating:  73%|███████▎  | 143/195 [00:23<00:08,  6.19it/s]

Evaluating:  74%|███████▍  | 144/195 [00:23<00:08,  6.19it/s]

Evaluating:  74%|███████▍  | 145/195 [00:23<00:08,  6.20it/s]

Evaluating:  75%|███████▍  | 146/195 [00:23<00:07,  6.21it/s]

Evaluating:  75%|███████▌  | 147/195 [00:24<00:07,  6.21it/s]

Evaluating:  76%|███████▌  | 148/195 [00:24<00:07,  6.22it/s]

Evaluating:  76%|███████▋  | 149/195 [00:24<00:07,  6.22it/s]

Evaluating:  77%|███████▋  | 150/195 [00:24<00:07,  6.22it/s]

Evaluating:  77%|███████▋  | 151/195 [00:24<00:07,  6.21it/s]

Evaluating:  78%|███████▊  | 152/195 [00:24<00:06,  6.20it/s]

Evaluating:  78%|███████▊  | 153/195 [00:25<00:09,  4.57it/s]

Evaluating:  79%|███████▉  | 154/195 [00:25<00:08,  4.96it/s]

Evaluating:  79%|███████▉  | 155/195 [00:25<00:07,  5.27it/s]

Evaluating:  80%|████████  | 156/195 [00:25<00:07,  5.5

{"eval_acc": 0.659601798330122, "eval_f1": 0.659570202275225, "eval_mcc": 0.3192470800803493, "eval_auc": 0.7148526058390066, "eval_precision": 0.6596512019437091, "eval_recall": 0.6595958829294692, "learning_rate": 1.1408199643493762e-07, "loss": 0.5267461937665939, "step": 3100}



Epoch: 100%|██████████| 4/4 [43:17<00:00, 649.37s/it]
05/25/2021 16:34:21 - INFO - __main__ -    global_step = 3116, average loss = 0.5995995346432855
05/25/2021 16:34:21 - INFO - __main__ -   Saving model checkpoint to /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/
05/25/2021 16:34:21 - INFO - transformers.configuration_utils -   Configuration saved in /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/config.json
05/25/2021 16:34:22 - INFO - transformers.modeling_utils -   Model weights saved in /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/pytorch_model.bin
05/25/2021 16:34:22 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/config.json
05/25/2021 16:34:22 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForLongSequenceClassificationCat"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos

<class 'transformers.tokenization_dna.DNATokenizer'>
<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 16:34:27 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_6mer/cached_dev_6-new-12w-0_2048_dnaprom
05/25/2021 16:34:27 - INFO - __main__ -   ***** Running evaluation  *****
05/25/2021 16:34:27 - INFO - __main__ -     Num examples = 1557
05/25/2021 16:34:27 - INFO - __main__ -     Batch size = 8
Evaluating: 100%|██████████| 195/195 [00:31<00:00,  6.13it/s]
05/25/2021 16:34:59 - INFO - __main__ -   ***** Eval results  *****
05/25/2021 16:34:59 - INFO - __main__ -     acc = 0.6602440590879898
05/25/2021 16:34:59 - INFO - __main__ -     auc = 0.7148262058997263
05/25/2021 16:34:59 - INFO - __main__ -     f1 = 0.6602081771688284
05/25/2021 16:34:59 - INFO - __main__ -     mcc = 0.32053893575416126
05/25/2021 16:34:59 - INFO - __main__ -     precision = 0.660301210586608
05/25/2021 16:34:59 - INFO - __main__ -     recall = 0.6602377314532176


In [20]:
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna6 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/ \
    --task_name dnaprom \
    --do_predict \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_6mer \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_aT/results_6mer/

05/25/2021 16:34:59 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
05/25/2021 16:34:59 - INFO - transformers.configuration_utils -   loading configuration file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/config.json
05/25/2021 16:34:59 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForLongSequenceClassificationCat"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "do_sample": false,
  "eos_token_ids": 0,
  "finetuning_task": "dnaprom",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1
  },
  "layer_norm_eps": 1e-12,
  "length_penalty": 1.0,
  "max_length": 20,
  "max_position_embeddings": 512,
  "model_type

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 16:35:02 - INFO - transformers.tokenization_utils -   loading file https://raw.githubusercontent.com/jerryji1993/DNABERT/master/src/transformers/dnabert-config/bert-config-6/vocab.txt from cache at /home/mgill/.cache/torch/transformers/ea1474aad40c1c8ed4e1cb7c11345ddda6df27a857fb29e1d4c901d9b900d32d.26f8bd5a32e49c2a8271a46950754a4a767726709b7741c68723bc1db840a87e
05/25/2021 16:35:02 - INFO - transformers.modeling_utils -   loading weights file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/output_data_6mer/pytorch_model.bin
05/25/2021 16:35:04 - INFO - __main__ -   finish loading model
05/25/2021 16:35:04 - INFO - __main__ -   Training/evaluation parameters Namespace(adam_epsilon=1e-08, attention_probs_dropout_prob=0.1, beta1=0.9, beta2=0.999, cache_dir='', config_name='', data_dir='/group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_6mer', device=device(type='cuda'), do_ensemble_pred=False, do_eval=False, do_lower_case=False, do_predict=True, do_train=False, do_vi

<class 'transformers.tokenization_dna.DNATokenizer'>


05/25/2021 16:35:06 - INFO - __main__ -   Loading features from cached file /group/pawsey0149/mgill/dl_playground/DNABERT_aT/input_data_6mer/cached_dev_2048_dnaprom
05/25/2021 16:35:06 - INFO - __main__ -   ***** Running prediction  *****
05/25/2021 16:35:06 - INFO - __main__ -     Num examples = 1557
05/25/2021 16:35:06 - INFO - __main__ -     Batch size = 32
Predicting:   0%|          | 0/49 [00:00<?, ?it/s]/home/mgill/.local/lib/python3.8/site-packages/torch/nn/parallel/_functions.py:61: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
Predicting: 100%|██████████| 49/49 [00:24<00:00,  1.99it/s]
05/25/2021 16:35:31 - INFO - __main__ -   ***** Pred results  *****
05/25/2021 16:35:31 - INFO - __main__ -     acc = 0.6602440590879898
05/25/2021 16:35:31 - INFO - __main__ -     auc = 0.7148262058997263
05/25/2021 16:35:31 - INFO - __main__ - 